In [1]:
import requests
import pandas as pd
import matplotlib.pyplot as plt
import json
from pandas import json_normalize
import petpy
import time
import sys
import time

%matplotlib inline
pd.set_option('display.max_columns', None)

In [2]:
# Open json to access key & secret
with open('keys.json') as fi:
    credentials = json.load(fi) 

In [3]:
# Access api key & secret
key = credentials['api_key_2']
secret = credentials['secret_2']

## Adopted Dogs

In [4]:
# Get token
token_url = 'https://api.petfinder.com/v2/oauth2/token'
token_data = {
    'grant_type': 'client_credentials',
    'client_id': key,
    'client_secret': secret
}

# Send post request to get token & extract token
response = requests.post(token_url, data=token_data)
access_token = response.json()['access_token'] 

# Create base url & headers with token access
base_url = 'https://api.petfinder.com/v2/animals'
headers = {'Authorization': f'Bearer {access_token}'}

# Create parameters
params = {
    'type': 'dog',
    'status': 'adopted', 
    'before': '2023-12-31T23:59:59+00:00',
    'after': '2023-01-01T00:00:00+00:00',
    'location': 'Nashville, TN',
    'distance': 300,
    'limit': 100 
}

response = requests.get(base_url, headers=headers, params=params)
res = response.json()
print(response)
res

<Response [200]>


{'animals': [{'id': 70208162,
   'organization_id': 'AL386',
   'url': 'https://www.petfinder.com/dog/rosey-70208162/al/guntersville/marshall-county-al-animal-control-al386/?referrer_id=e44a9da8-6fd6-41a3-9209-654475f5128b&utm_source=api&utm_medium=partnership&utm_content=e44a9da8-6fd6-41a3-9209-654475f5128b',
   'type': 'Dog',
   'species': 'Dog',
   'breeds': {'primary': 'Bull Terrier',
    'secondary': None,
    'mixed': True,
    'unknown': False},
   'colors': {'primary': 'White / Cream', 'secondary': None, 'tertiary': None},
   'age': 'Adult',
   'gender': 'Female',
   'size': 'Large',
   'coat': 'Short',
   'attributes': {'spayed_neutered': False,
    'house_trained': False,
    'declawed': None,
    'special_needs': False,
    'shots_current': False},
   'environment': {'children': None, 'dogs': None, 'cats': None},
   'tags': ['Friendly',
    'Affectionate',
    'Playful',
    'Funny',
    'Quiet',
    'Curious',
    'Loves kisses',
    'Couch Potato'],
   'name': 'rosey',
   

In [5]:
# Get initial response
response = requests.get(base_url, headers=headers, params=params)

# Check if the initial response is successful
if response.status_code != 200:
    print(f"Failed: {response.status_code}")
else:
# Get Json and extract pagination info
    res = response.json()
    pagination_info = res.get('pagination', {})
    total_pages = pagination_info.get('total_pages', 0)
    all_pages = []

# Store data from response
    if 'animals' in res:
        all_pages.extend(res['animals'])

# Loop through remaining pages and retrieve data
    for page_num in range(2, total_pages + 1): # From page 2
        params['page'] = page_num
        for attempt in range(11): 
            response = requests.get(base_url, headers=headers, params=params)
            if response.status_code == 200:
                res = response.json()
                if 'animals' in res:
                    all_pages.extend(res['animals'])
                break
            else:
                if attempt == 10:
                    print(f"Page {page_num} failed after retries.")
                break

    print("Successful")
    print(len(all_pages))
    print(f"Total Pages: {total_pages}")

Successful
62328
Total Pages: 624


In [6]:
dogs = json_normalize(all_pages)
print(dogs.shape)
dogs.head()

(62328, 50)


id organization_id  \
0  70208162           AL386   
1  70208130           AL386   
2  70207589          TN1010   
3  70207388            MS64   
4  70207380            SC11   

                                                 url type species    age  \
0  https://www.petfinder.com/dog/rosey-70208162/a...  Dog     Dog  Adult   
1  https://www.petfinder.com/dog/fancy-70208130/a...  Dog     Dog  Adult   
2  https://www.petfinder.com/dog/sir-70207589/tn/...  Dog     Dog  Young   
3  https://www.petfinder.com/dog/emma-70207388/ms...  Dog     Dog   Baby   
4  https://www.petfinder.com/dog/mystique-oct-23-...  Dog     Dog  Adult   

   gender    size   coat                                               tags  \
0  Female   Large  Short  [Friendly, Affectionate, Playful, Funny, Quiet...   
1  Female   Large   None                                                 []   
2    Male  Medium   None                                                 []   
3  Female  Medium   None                                                 []   
4  Female   Large   None                                                 []   

                                                name  \
0                                              rosey   
1                                              Fancy   
2                                                Sir   
3                                               Emma   
4  Mystique Oct 23 - in foster care in Charleston sc   

                                         description  \
0  This goofy girl is Rosie! At intake, Rosie was...   
1  Fancy is a two-year-old Pitt female now weighi...   
2                                               None   
3                    Emma is about three months old.   
4  NOT IN VPDate into Rescue: 10/1/2023\nReason f...   

                 organization_animal_id  \
0                                  None   
1                                  None   
2  783acbd2-9929-4359-9c1b-d117e809c775   
3                                  None   
4                      19844035-23-0379   

                                              photos videos   status  \
0  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
1  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
2  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
3  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
4  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   

          status_changed_at              published_at  distance  \
0  2024-01-10T22:10:04+0000  2023-12-31T23:49:40+0000  133.3947   
1  2024-01-22T19:35:18+0000  2023-12-31T23:36:54+0000  133.3947   
2  2024-01-04T22:32:27+0000  2023-12-31T22:02:56+0000  163.8548   
3  2024-01-20T18:15:45+0000  2023-12-31T21:35:14+0000  284.5961   
4  2023-12-31T21:33:45+0000  2023-12-31T21:33:43+0000  295.6223   

       breeds.primary breeds.secondary  breeds.mixed  breeds.unknown  \
0        Bull Terrier             None          True           False   
1        Bull Terrier             None         False           False   
2      Boston Terrier             None         False           False   
3  Labrador Retriever             None          True           False   
4     Standard Poodle             None         False           False   

  colors.primary colors.secondary colors.tertiary  attributes.spayed_neutered  \
0  White / Cream             None            None                       False   
1          Black    White / Cream            None                       False   
2           None             None            None                        True   
3           None             None            None                        True   
4           None             None            None                        True   

   attributes.house_trained attributes.declawed  attributes.special_needs  \
0                     False                None                     False   
1                     False                None

In [7]:
# Filter only TN 
dogs = dogs[dogs['contact.address.state']=='TN']
dogs.shape

(17879, 50)

## Adoptable ogs

In [8]:
# Get token
token_url = 'https://api.petfinder.com/v2/oauth2/token'
token_data = {
    'grant_type': 'client_credentials',
    'client_id': key,
    'client_secret': secret
}

# Send post request to get token & extract token
response = requests.post(token_url, data=token_data)
access_token = response.json()['access_token']

# Create base url & headers with token access
base_url = 'https://api.petfinder.com/v2/animals'
headers = {'Authorization': f'Bearer {access_token}'}

# Create parameters
params = {
    'type': 'dog',
    'status': 'adoptable', 
    'before': '2023-12-31T23:59:59+00:00',
    'after': '2023-01-01T00:00:00+00:00',
    'location': 'Nashville, TN',
    'distance': 300,
    'limit': 100 
}

response = requests.get(base_url, headers=headers, params=params)
res = response.json()
print(response)
res

<Response [200]>


{'animals': [{'id': 70208186,
   'organization_id': 'IN695',
   'url': 'https://www.petfinder.com/dog/darcy-70208186/in/seymour/clancys-dream-inc-in695/?referrer_id=e44a9da8-6fd6-41a3-9209-654475f5128b&utm_source=api&utm_medium=partnership&utm_content=e44a9da8-6fd6-41a3-9209-654475f5128b',
   'type': 'Dog',
   'species': 'Dog',
   'breeds': {'primary': 'Border Collie',
    'secondary': None,
    'mixed': False,
    'unknown': False},
   'colors': {'primary': 'Black',
    'secondary': 'White / Cream',
    'tertiary': None},
   'age': 'Young',
   'gender': 'Female',
   'size': 'Medium',
   'coat': 'Short',
   'attributes': {'spayed_neutered': True,
    'house_trained': True,
    'declawed': None,
    'special_needs': False,
    'shots_current': True},
   'environment': {'children': True, 'dogs': True, 'cats': None},
   'tags': ['Friendly',
    'Affectionate',
    'Loyal',
    'Gentle',
    'Playful',
    'Smart',
    'Athletic',
    'Curious',
    'Couch Potato'],
   'name': 'Darcy',
   

In [9]:
# Get initial response
response = requests.get(base_url, headers=headers, params=params)

# Check if the initial response is successful
if response.status_code != 200:
    print(f"Failed: {response.status_code}")
else:
# Get Json and extract pagination info
    res = response.json()
    pagination_info = res.get('pagination', {})
    total_pages = pagination_info.get('total_pages', 0)
    all_pages = []

# Store data from response
    if 'animals' in res:
        all_pages.extend(res['animals'])

# Loop through remaining pages and retrieve data
    for page_num in range(2, total_pages + 1): # From page 2
        params['page'] = page_num
        for attempt in range(11): 
            response = requests.get(base_url, headers=headers, params=params)
            if response.status_code == 200:
                res = response.json()
                if 'animals' in res:
                    all_pages.extend(res['animals'])
                break
            else:
                if attempt == 10:
                    print(f"Page {page_num} failed after retries.")
                break

    print("Successful")
    print(len(all_pages))
    print(f"Total Pages: {total_pages}")

Successful
11322
Total Pages: 114


In [10]:
dogs2 = json_normalize(all_pages)
print(dogs2.shape)
dogs2.head()

(11322, 50)


id organization_id  \
0  70208186           IN695   
1  70208161           IN695   
2  70208047           MO228   
3  70207426            TN98   
4  70207357            MS64   

                                                 url type species    age  \
0  https://www.petfinder.com/dog/darcy-70208186/i...  Dog     Dog  Young   
1  https://www.petfinder.com/dog/logan-70208161/i...  Dog     Dog  Young   
2  https://www.petfinder.com/dog/samoa-70208047/m...  Dog     Dog  Young   
3  https://www.petfinder.com/dog/suzzie-70207426/...  Dog     Dog   Baby   
4  https://www.petfinder.com/dog/evan-70207357/ms...  Dog     Dog   Baby   

   gender    size   coat                                               tags  \
0  Female  Medium  Short  [Friendly, Affectionate, Loyal, Gentle, Playfu...   
1    Male  Medium  Short  [Friendly, Affectionate, Loyal, Gentle, Playfu...   
2  Female  Medium   None                                                 []   
3  Female  Medium  Short  [Friendly, Affectionate, Playful, Smart, Curio...   
4    Male  Medium   None                                                 []   

     name                                        description  \
0   Darcy  Darcy was found wandering with Logan, who we t...   
1   Logan  Darcy was found wandering with Logan, who we t...   
2   SAMOA  Samoa is a sweet, medium-energy girl who walks...   
3  Suzzie  Suzzie is a loveable, very chill, 12 week old ...   
4    Evan  Evan is about three months old and weighs fift...   

  organization_animal_id                                             photos  \
0                   None  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
1                   None  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
2                A292482  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
3                   None  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
4                   None  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   

  videos     status         status_changed_at              published_at  \
0     []  adoptable  2023-12-31T23:59:23+0000  2023-12-31T23:59:22+0000   
1     []  adoptable  2023-12-31T23:49:27+0000  2023-12-31T23:49:25+0000   
2     []  adoptable  2023-12-31T23:19:22+0000  2023-12-31T23:19:19+0000   
3     []  adoptable  2023-12-31T21:41:58+0000  2023-12-31T21:41:50+0000   
4     []  adoptable  2024-01-04T03:49:24+0000  2023-12-31T21:30:08+0000   

   distance      breeds.primary  breeds.secondary  breeds.mixed  \
0  199.1141       Border Collie              None         False   
1  199.1141       Border Collie              None         False   
2  258.5021    Pit Bull Terrier              None         False   
3   46.5967           Chihuahua  Pit Bull Terrier          True   
4  284.5961  Labrador Retriever              None          True   

   breeds.unknown           colors.primary   colors.secondary colors.tertiary  \
0           False                    Black      White / Cream            None   
1           False                    Black      White / Cream            None   
2           False                     None               None            None   
3           False  Red / Chestnut / Orange  Brown / Chocolate   White / Cream   
4           False                     None               None            None   

   attributes.spayed_neutered  attributes.house_trained attributes.declawed  \
0                        True                      True                None   
1                        True                      True                None   
2                        True                     False                None   
3                        True                      True                None   
4                        True                     False                None   

   attributes.special_needs  attributes.shots_current environment.children  \
0                     False                      True                 True   
1                     False                      True     

In [11]:
# Filter only TN
dogs2 = dogs2[dogs2['contact.address.state']=='TN']
dogs2.shape

(2014, 50)

In [12]:
# Combine dataframes into one
dogs = pd.concat([dogs, dogs2], ignore_index=True)
print(dogs.shape)
dogs.head()

(19893, 50)


id organization_id  \
0  70207589          TN1010   
1  70206826           TN297   
2  70206549           TN411   
3  70206444           TN411   
4  70206047           TN411   

                                                 url type species    age  \
0  https://www.petfinder.com/dog/sir-70207589/tn/...  Dog     Dog  Young   
1  https://www.petfinder.com/dog/daisy-70206826/t...  Dog     Dog   Baby   
2  https://www.petfinder.com/dog/jessie-momma-dog...  Dog     Dog  Adult   
3  https://www.petfinder.com/dog/rolo-70206444/tn...  Dog     Dog   Baby   
4  https://www.petfinder.com/dog/trixie-toy-story...  Dog     Dog   Baby   

   gender    size    coat                                               tags  \
0    Male  Medium    None                                                 []   
1  Female  Medium    None                                                 []   
2  Female   Large  Medium  [Friendly, Affectionate, Loyal, Gentle, Smart,...   
3    Male   Large  Medium  [Friendly, Playful, Affectionate, Funny, Athle...   
4  Female  Medium  Medium  [Friendly, Affectionate, Loyal, Playful, Brave...   

                                     name  \
0                                     Sir   
1                                   Daisy   
2  Jessie (Momma Dog to Toy Story Litter)   
3                                    Rolo   
4               Trixie (Toy Story Litter)   

                                         description  \
0                                               None   
1  You can fill out an adoption application onlin...   
2  Meet Jessie.  She is the momma of the 10 puppp...   
3  Rolo is a single puppy we rescued when he was ...   
4  Meet Trixie.  She is one of the 10 pupppies bo...   

                 organization_animal_id  \
0  783acbd2-9929-4359-9c1b-d117e809c775   
1                              19975012   
2                                  None   
3                                  None   
4                                  None   

                                              photos videos   status  \
0  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
1  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
2  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
3  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
4  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   

          status_changed_at              published_at  distance  \
0  2024-01-04T22:32:27+0000  2023-12-31T22:02:56+0000  163.8548   
1  2023-12-31T20:19:46+0000  2023-12-31T20:19:44+0000   11.8361   
2  2024-01-27T01:07:06+0000  2023-12-31T20:03:20+0000   15.0118   
3  2024-01-04T14:34:35+0000  2023-12-31T19:48:24+0000   15.0118   
4  2023-12-31T19:10:28+0000  2023-12-31T19:04:10+0000   15.0118   

       breeds.primary breeds.secondary  breeds.mixed  breeds.unknown  \
0      Boston Terrier             None         False           False   
1             Terrier             None          True           False   
2  Labrador Retriever         Shepherd          True           False   
3  Labrador Retriever         Shepherd          True           False   
4  Labrador Retriever         Shepherd          True           False   

                     colors.primary             colors.secondary  \
0                              None                         None   
1                              None                         None   
2  Tricolor (Brown, Black, & White)                         None   
3                             Black  Yellow / Tan / Blond / Fawn   
4                           Brindle                White / Cream   

  colors.tertiary  attributes.spayed_neutered  attributes.house_trained  \
0            None                        True                     False   
1            None                       False                     False   
2            None                       False                      True   
3            None                      

In [13]:
# Export to CSV
dogs.to_csv('../data/dogs.csv', index=False)

## Adopted Cats

In [21]:
# Get token
token_url = 'https://api.petfinder.com/v2/oauth2/token'
token_data = {
    'grant_type': 'client_credentials',
    'client_id': key,
    'client_secret': secret
}

# Send post request to get token & extract token
response = requests.post(token_url, data=token_data)
access_token = response.json()['access_token']

# Create base url & headers with token access
base_url = 'https://api.petfinder.com/v2/animals'
headers = {'Authorization': f'Bearer {access_token}'}

# Create parameters
params = {
    'type' : 'Cat',
    'status': 'adopted', 
    'before': '2023-12-31T23:59:59+00:00',
    'after': '2023-01-01T00:00:00+00:00',
    'location': 'Nashville, TN',
    'distance': 300,
    'limit': 100 
}

response = requests.get(base_url, headers=headers, params=params)
res = response.json()
print(response)
res

<Response [200]>


{'animals': [{'id': 70208019,
   'organization_id': 'TN801',
   'url': 'https://www.petfinder.com/cat/madame-kitty-70208019/tn/chattanooga/meow-meow-kitty-rescue-tn801/?referrer_id=faba0c62-7796-4d66-aba9-6ae4db9b200c&utm_source=api&utm_medium=partnership&utm_content=faba0c62-7796-4d66-aba9-6ae4db9b200c',
   'type': 'Cat',
   'species': 'Cat',
   'breeds': {'primary': 'Domestic Short Hair',
    'secondary': None,
    'mixed': False,
    'unknown': False},
   'colors': {'primary': 'Calico', 'secondary': None, 'tertiary': None},
   'age': 'Young',
   'gender': 'Female',
   'size': 'Medium',
   'coat': 'Short',
   'attributes': {'spayed_neutered': True,
    'house_trained': True,
    'declawed': False,
    'special_needs': False,
    'shots_current': True},
   'environment': {'children': True, 'dogs': None, 'cats': None},
   'tags': [],
   'name': 'Madame Kitty ',
   'description': 'Meet Madame Kitty, a 2 year old DSH cat. She is a very sweet girl and has lived all her...',
   'organizati

In [22]:
# Get initial response
response = requests.get(base_url, headers=headers, params=params)

# Check if the initial response is successful
if response.status_code != 200:
    print(f"Failed: {response.status_code}")
else:
# Get Json and extract pagination info
    res = response.json()
    pagination_info = res.get('pagination', {})
    total_pages = pagination_info.get('total_pages', 0)
    all_pages = []

# Store data from response
    if 'animals' in res:
        all_pages.extend(res['animals'])

# Loop through remaining pages and retrieve data
    for page_num in range(2, total_pages + 1): # From page 2
        params['page'] = page_num
        for attempt in range(11): 
            response = requests.get(base_url, headers=headers, params=params)
            if response.status_code == 200:
                res = response.json()
                if 'animals' in res:
                    all_pages.extend(res['animals'])
                break
            else:
                if attempt == 10:
                    print(f"Page {page_num} failed after retries.")
                break

    print("Successful")
    print(len(all_pages))
    print(f"Total Pages: {total_pages}")

Successful
52328
Total Pages: 524


In [23]:
# Normalize json
cats = json_normalize(all_pages)
print(cats.shape)
cats.head()

(52328, 50)


id organization_id  \
0  70208019           TN801   
1  70207823           TN597   
2  70207459           AL502   
3  70207450           TN369   
4  70207180           KY105   

                                                 url type species    age  \
0  https://www.petfinder.com/cat/madame-kitty-702...  Cat     Cat  Young   
1  https://www.petfinder.com/cat/truffles-7020782...  Cat     Cat   Baby   
2  https://www.petfinder.com/cat/lane-70207459/al...  Cat     Cat  Young   
3  https://www.petfinder.com/cat/teetee-70207450/...  Cat     Cat   Baby   
4  https://www.petfinder.com/cat/dusty-70207180/k...  Cat     Cat  Young   

   gender    size   coat                                           tags  \
0  Female  Medium  Short                                             []   
1  Female   Small  Short              [Friendly, Affectionate, Playful]   
2  Female  Medium   None                                             []   
3    Male   Small  Short              [Friendly, Affectionate, Playful]   
4    Male  Medium  Short  [Affectionate, Gentle, Smart, Curious, Brave]   

            name                                        description  \
0  Madame Kitty   Meet Madame Kitty, a 2 year old DSH cat. She i...   
1       Truffles  Truffles is the new kid on the block.  This pr...   
2           Lane  Lane is a BEAUTIFUL tabby girl! The pic does n...   
3         TeeTee  Meet TeeTee! He is an extremely adorable and s...   
4          Dusty  Dusty\n8 months\nMale\nBuff\nAdoption Fee: $10...   

                 organization_animal_id  \
0                                  None   
1                                  None   
2  450018f1-5d24-406d-99e4-32504a45d698   
3                               1207-23   
4                                  None   

                                              photos videos   status  \
0  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
1  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
2  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
3  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
4  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   

          status_changed_at              published_at  distance  \
0  2024-01-22T13:31:21+0000  2023-12-31T23:19:08+0000  120.4729   
1  2024-01-18T00:05:29+0000  2023-12-31T22:40:37+0000   33.2060   
2  2024-01-10T16:47:02+0000  2023-12-31T21:47:15+0000  171.2332   
3  2024-01-06T00:56:45+0000  2023-12-31T21:45:47+0000    7.6471   
4  2024-01-30T17:30:21+0000  2023-12-31T21:07:07+0000  154.8389   

        breeds.primary breeds.secondary  breeds.mixed  breeds.unknown  \
0  Domestic Short Hair             None         False           False   
1        Dilute Calico             None          True           False   
2  Domestic Short Hair             None         False           False   
3  Domestic Short Hair             None         False           False   
4  Domestic Short Hair             None         False           False   

                 colors.primary   colors.secondary colors.tertiary  \
0                        Calico               None            None   
1                 Dilute Calico  Brown / Chocolate            None   
2                          None               None            None   
3  Tabby (Gray / Blue / Silver)               None            None   
4             Buff / Tan / Fawn               None            None   

   attributes.spayed_neutered  attributes.house_trained  attributes.declawed  \
0                        True                      True                False   
1                        True                      True                False   
2                        True                      True                False   
3                        True                      True                False   
4                        True                      True                False   

   attributes.special_needs  attributes.shots_curre

In [24]:
# Filter TN only
cats = cats[cats['contact.address.state']=='TN']
cats.shape

(13157, 50)

## Adoptable Cats

In [25]:
# Get token
token_url = 'https://api.petfinder.com/v2/oauth2/token'
token_data = {
    'grant_type': 'client_credentials',
    'client_id': key,
    'client_secret': secret
}

# Send post request to get token & extract token
response = requests.post(token_url, data=token_data)
access_token = response.json()['access_token']

# Create base url & headers with token access
base_url = 'https://api.petfinder.com/v2/animals'
headers = {'Authorization': f'Bearer {access_token}'}

# Create parameters
params = {
    'type': 'Cat',
    'status': 'adoptable', 
    'before': '2023-12-31T23:59:59+00:00',
    'after': '2023-01-01T00:00:00+00:00',
    'location': 'Nashville, TN',
    'distance': 300,
    'limit': 100 
}

response = requests.get(base_url, headers=headers, params=params)
res = response.json()
print(response)
res

<Response [200]>


{'animals': [{'id': 70181588,
   'organization_id': 'IN723',
   'url': 'https://www.petfinder.com/cat/ozcar-70181588/in/lafayette/loving-paws-animal-center-in723/?referrer_id=faba0c62-7796-4d66-aba9-6ae4db9b200c&utm_source=api&utm_medium=partnership&utm_content=faba0c62-7796-4d66-aba9-6ae4db9b200c',
   'type': 'Cat',
   'species': 'Cat',
   'breeds': {'primary': 'Tabby',
    'secondary': 'Domestic Short Hair',
    'mixed': True,
    'unknown': False},
   'colors': {'primary': 'Tabby (Brown / Chocolate)',
    'secondary': 'Tabby (Buff / Tan / Fawn)',
    'tertiary': None},
   'age': 'Young',
   'gender': 'Male',
   'size': 'Medium',
   'coat': 'Short',
   'attributes': {'spayed_neutered': True,
    'house_trained': True,
    'declawed': False,
    'special_needs': False,
    'shots_current': True},
   'environment': {'children': False, 'dogs': False, 'cats': True},
   'tags': ['Affectionate', 'Shy', 'Playful'],
   'name': 'Ozcar',
   'description': 'Ozcar is very shy with new people but

In [26]:
# Get initial response
response = requests.get(base_url, headers=headers, params=params)

# Check if the initial response is successful
if response.status_code != 200:
    print(f"Failed: {response.status_code}")
else:
# Get Json and extract pagination info
    res = response.json()
    pagination_info = res.get('pagination', {})
    total_pages = pagination_info.get('total_pages', 0)
    all_pages = []

# Store data from response
    if 'animals' in res:
        all_pages.extend(res['animals'])

# Loop through remaining pages and retrieve data
    for page_num in range(2, total_pages + 1): # From page 2
        params['page'] = page_num
        for attempt in range(11): 
            response = requests.get(base_url, headers=headers, params=params)
            if response.status_code == 200:
                res = response.json()
                if 'animals' in res:
                    all_pages.extend(res['animals'])
                break
            else:
                if attempt == 10:
                    print(f"Page {page_num} failed after retries.")
                break

    print("Successful")
    print(len(all_pages))
    print(f"Total Pages: {total_pages}")

Successful
6484
Total Pages: 65


In [27]:
cats2 = json_normalize(all_pages)
print(cats2.shape)
cats2.head()

(6484, 50)


id organization_id  \
0  70181588           IN723   
1  70208184           GA512   
2  70207606           TN671   
3  70207605           TN671   
4  70207375           AL502   

                                                 url type species    age  \
0  https://www.petfinder.com/cat/ozcar-70181588/i...  Cat     Cat  Young   
1  https://www.petfinder.com/cat/dorothy-70208184...  Cat     Cat  Young   
2  https://www.petfinder.com/cat/evie-mb-70207606...  Cat     Cat  Adult   
3  https://www.petfinder.com/cat/colby-mb-7020760...  Cat     Cat  Adult   
4  https://www.petfinder.com/cat/johnnie-70207375...  Cat     Cat  Young   

   gender    size   coat                                              tags  \
0    Male  Medium  Short                      [Affectionate, Shy, Playful]   
1  Female  Medium  Short  [Affectionate, Gentle, Playful, Quiet, Friendly]   
2  Female  Medium   None                                                []   
3    Male  Medium   None                                                []   
4  Female  Medium   None                                                []   

       name                                        description  \
0     Ozcar  Ozcar is very shy with new people but is super...   
1   Dorothy  Dorothy is a playful, 1-2 year old cow kitty w...   
2   Evie mb  Another CHILLIN cat -Meet our girl Evie - Appr...   
3  Colby mb  This boy is simply CHILLIN. Meet Colby- Approx...   
4   Johnnie  Johnnie is a precious girl not to mention so c...   

                 organization_animal_id  \
0                                  None   
1                                  None   
2                              20115405   
3                              20115403   
4  c7d483c7-f246-4d2b-a854-aad9ae500a39   

                                              photos  \
0  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
1  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
2  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
3  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
4  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   

                                              videos     status  \
0                                                 []  adoptable   
1  [{'embed': '<iframe title="Video" frameborder=...  adoptable   
2                                                 []  adoptable   
3                                                 []  adoptable   
4                                                 []  adoptable   

          status_changed_at              published_at  distance  \
0  2023-12-31T23:56:52+0000  2023-12-31T23:56:49+0000  293.8792   
1  2023-12-31T23:56:38+0000  2023-12-31T23:56:33+0000  214.4646   
2  2023-12-31T22:05:43+0000  2023-12-31T22:05:40+0000   24.6827   
3  2023-12-31T22:05:43+0000  2023-12-31T22:05:40+0000   24.6827   
4  2023-12-31T21:33:40+0000  2023-12-31T21:33:38+0000  171.2332   

         breeds.primary     breeds.secondary  breeds.mixed  breeds.unknown  \
0                 Tabby  Domestic Short Hair          True           False   
1    American Shorthair                 None         False           False   
2  Domestic Medium Hair                 None          True           False   
3   Domestic Short Hair                 None          True           False   
4   Domestic Short Hair                 None         False           False   

              colors.primary           colors.secondary colors.tertiary  \
0  Tabby (Brown / Chocolate)  Tabby (Buff / Tan / Fawn)            None   
1     Black & White / Tuxedo                       None            None   
2             Orange & White                       None            None   
3     Black & White / Tuxedo                       None            None   
4                       None                       None            None   

   attributes.spayed_neutered  attributes.house_trained  attributes.declawed  \
0                        True                      True                False   
1                

In [28]:
cats2 = cats2[cats2['contact.address.state']=='TN']
cats2.shape

(1083, 50)

In [29]:
# Combine dataframes into one
cats = pd.concat([cats, cats2], ignore_index=True)
print(cats.shape)
cats.head()

(14240, 50)


id organization_id  \
0  70208019           TN801   
1  70207823           TN597   
2  70207450           TN369   
3  70203376            TN90   
4  70203375            TN90   

                                                 url type species    age  \
0  https://www.petfinder.com/cat/madame-kitty-702...  Cat     Cat  Young   
1  https://www.petfinder.com/cat/truffles-7020782...  Cat     Cat   Baby   
2  https://www.petfinder.com/cat/teetee-70207450/...  Cat     Cat   Baby   
3  https://www.petfinder.com/cat/ac-25055-7020337...  Cat     Cat  Young   
4  https://www.petfinder.com/cat/ac-25035-7020337...  Cat     Cat  Young   

   gender    size   coat                               tags           name  \
0  Female  Medium  Short                                 []  Madame Kitty    
1  Female   Small  Short  [Friendly, Affectionate, Playful]       Truffles   
2    Male   Small  Short  [Friendly, Affectionate, Playful]         TeeTee   
3    Male  Medium   None                                 []       AC 25055   
4  Female  Medium   None                                 []       AC 25035   

                                         description organization_animal_id  \
0  Meet Madame Kitty, a 2 year old DSH cat. She i...                   None   
1  Truffles is the new kid on the block.  This pr...                   None   
2  Meet TeeTee! He is an extremely adorable and s...                1207-23   
3                                               None              A2023C688   
4                                               None              A2023C687   

                                              photos videos   status  \
0  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
1  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
2  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
3                                                 []     []  adopted   
4                                                 []     []  adopted   

          status_changed_at              published_at  distance  \
0  2024-01-22T13:31:21+0000  2023-12-31T23:19:08+0000  120.4729   
1  2024-01-18T00:05:29+0000  2023-12-31T22:40:37+0000   33.2060   
2  2024-01-06T00:56:45+0000  2023-12-31T21:45:47+0000    7.6471   
3  2023-12-31T10:03:59+0000  2023-12-31T10:03:58+0000  223.6873   
4  2023-12-31T10:03:57+0000  2023-12-31T10:03:56+0000  223.6873   

        breeds.primary breeds.secondary  breeds.mixed  breeds.unknown  \
0  Domestic Short Hair             None         False           False   
1        Dilute Calico             None          True           False   
2  Domestic Short Hair             None         False           False   
3  Domestic Short Hair             None         False           False   
4  Domestic Short Hair             None         False           False   

                 colors.primary   colors.secondary colors.tertiary  \
0                        Calico               None            None   
1                 Dilute Calico  Brown / Chocolate            None   
2  Tabby (Gray / Blue / Silver)               None            None   
3                          None               None            None   
4                          None               None            None   

   attributes.spayed_neutered  attributes.house_trained  attributes.declawed  \
0                        True                      True                False   
1                        True                      True                False   
2                        True                      True                False   
3                       False                     False                False   
4                       False                     False                False   

   attributes.special_needs  attributes.shots_current environment.children  \
0                     False                      True                 True   
1                     False                      True                 True   
2         

In [32]:
# Export to CSV
cats.to_csv('../data/cats.csv', index=False)

## Adopted horses

In [33]:
# Get token
token_url = 'https://api.petfinder.com/v2/oauth2/token'
token_data = {
    'grant_type': 'client_credentials',
    'client_id': key,
    'client_secret': secret
}

# Send post request to get token & extract token
response = requests.post(token_url, data=token_data)
access_token = response.json()['access_token']

# Create base url & headers with token access
base_url = 'https://api.petfinder.com/v2/animals'
headers = {'Authorization': f'Bearer {access_token}'}

# Create parameters
params = {
    'type' : 'horse',
    'status': 'adopted', 
    'before': '2023-12-31T23:59:59+00:00',
    'after': '2023-01-01T00:00:00+00:00',
    'location': 'Nashville, TN',
    'distance': 300,
    'limit': 100 
}

response = requests.get(base_url, headers=headers, params=params)
res = response.json()
print(response)
res

<Response [200]>


{'animals': [{'id': 70154683,
   'organization_id': 'TN801',
   'url': 'https://www.petfinder.com/horse/apple-jacks-70154683/tn/chattanooga/meow-meow-kitty-rescue-tn801/?referrer_id=faba0c62-7796-4d66-aba9-6ae4db9b200c&utm_source=api&utm_medium=partnership&utm_content=faba0c62-7796-4d66-aba9-6ae4db9b200c',
   'type': 'Horse',
   'species': 'Miniature Horse',
   'breeds': {'primary': 'Miniature Horse',
    'secondary': None,
    'mixed': False,
    'unknown': False},
   'colors': {'primary': 'Bay', 'secondary': 'Bay Roan', 'tertiary': 'Brown'},
   'age': 'Young',
   'gender': 'Male',
   'size': 'Small',
   'coat': None,
   'attributes': {'spayed_neutered': True,
    'house_trained': False,
    'declawed': None,
    'special_needs': False,
    'shots_current': True},
   'environment': {'children': True, 'dogs': None, 'cats': True},
   'tags': ['Loyal',
    'Gentle',
    'Friendly',
    'Protective',
    'Independent',
    'Quiet',
    'Curious'],
   'name': 'Apple Jacks ',
   'descriptio

In [34]:
# Get initial response
response = requests.get(base_url, headers=headers, params=params)

# Check if the initial response is successful
if response.status_code != 200:
    print(f"Failed: {response.status_code}")
else:
# Get Json and extract pagination info
    res = response.json()
    pagination_info = res.get('pagination', {})
    total_pages = pagination_info.get('total_pages', 0)
    all_pages = []

# Store data from response
    if 'animals' in res:
        all_pages.extend(res['animals'])

# Loop through remaining pages and retrieve data
    for page_num in range(2, total_pages + 1): # From page 2
        params['page'] = page_num
        for attempt in range(11): 
            response = requests.get(base_url, headers=headers, params=params)
            if response.status_code == 200:
                res = response.json()
                if 'animals' in res:
                    all_pages.extend(res['animals'])
                break
            else:
                if attempt == 10:
                    print(f"Page {page_num} failed after retries.")
                break

    print("Successful")
    print(len(all_pages))
    print(f"Total Pages: {total_pages}")

Successful
86
Total Pages: 1


In [35]:
horse = json_normalize(all_pages)
horse.head()

id organization_id  \
0  70154683           TN801   
1  70126343            GA33   
2  70057623           TN867   
3  70044014           WV164   
4  70030185            GA33   

                                                 url   type          species  \
0  https://www.petfinder.com/horse/apple-jacks-70...  Horse  Miniature Horse   
1  https://www.petfinder.com/horse/tonto-70126343...  Horse            Horse   
2  https://www.petfinder.com/horse/simon-70057623...  Horse            Horse   
3  https://www.petfinder.com/horse/arizona-700440...  Horse             Mule   
4  https://www.petfinder.com/horse/poncho-and-lef...  Horse           Donkey   

     age  gender    size  coat  \
0  Young    Male   Small  None   
1  Adult    Male   Large  None   
2  Adult    Male  Medium  None   
3  Adult  Female  Medium  None   
4  Adult    Male  Medium  None   

                                                tags              name  \
0  [Loyal, Gentle, Friendly, Protective, Independ...      Apple Jacks    
1                   [Friendly, Affectionate, Gentle]             Tonto   
2         [Affectionate, Friendly, Playful, Curious]             Simon   
3                                                 []           Arizona   
4                         [Gentle, Playful, Curious]  Poncho and Lefty   

                                         description organization_animal_id  \
0  Apple Jacks is a sweet miniature horse who was...                   None   
1  We got him from a local auction. He&#039;s a s...                   None   
2  Beautiful Bay gelding. In your pocket, has bee...                   None   
3  Arizona\n2011\nMule Pony\nGray\nMolly\n12.1hh ...                   None   
4  Poncho and Lefty are very good looking donkeys...                   None   

                                              photos  \
0  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
1                                                 []   
2  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
3  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
4  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   

                                              videos   status  \
0                                                 []  adopted   
1  [{'embed': '<iframe title="Video" frameborder=...  adopted   
2                                                 []  adopted   
3                                                 []  adopted   
4                                                 []  adopted   

          status_changed_at              published_at  distance  \
0  2024-01-03T15:56:09+0000  2023-12-26T22:30:12+0000  120.4751   
1  2024-01-03T00:48:25+0000  2023-12-22T16:42:35+0000  193.9479   
2  2024-01-13T04:14:13+0000  2023-12-16T07:05:38+0000   14.9344   
3  2024-01-12T03:45:13+0000  2023-12-15T05:16:42+0000  289.1093   
4  2024-01-26T00:44:20+0000  2023-12-14T03:39:21+0000  193.9479   

    breeds.primary breeds.secondary  breeds.mixed  breeds.unknown  \
0  Miniature Horse             None         False           False   
1    Paint / Pinto             None         False           False   
2           Morgan             None         False           False   
3             Mule             None         False           False   
4           Donkey             None          True           False   

  colors.primary colors.secondary colors.tertiary  attributes.spayed_neutered  \
0            Bay         Bay Roan           Brown                        True   
1          Pinto             None            None                        True   
2            Bay             None            None                       False   
3      Blue Roan             None            None                       False   
4           Gray             None            None                        True   

   attributes.house_trained attributes.declawed  attributes.special_needs  \
0                     False                None                     False   
1                     False  

In [36]:
horse = horse[horse['contact.address.state']=='TN']
horse.shape

(14, 50)

## Adoptable horses

In [37]:
# Get token
token_url = 'https://api.petfinder.com/v2/oauth2/token'
token_data = {
    'grant_type': 'client_credentials',
    'client_id': key,
    'client_secret': secret
}

# Send post request to get token & extract token
response = requests.post(token_url, data=token_data)
access_token = response.json()['access_token']

# Create base url & headers with token access
base_url = 'https://api.petfinder.com/v2/animals'
headers = {'Authorization': f'Bearer {access_token}'}

# Create parameters
params = {
    'type': 'horse',
    'status': 'adoptable', 
    'before': '2023-12-31T23:59:59+00:00',
    'after': '2023-01-01T00:00:00+00:00',
    'location': 'Nashville, TN',
    'distance': 300,
    'limit': 100 
}

response = requests.get(base_url, headers=headers, params=params)
res = response.json()
print(response)
res

<Response [200]>


{'animals': [{'id': 70172509,
   'organization_id': 'GA33',
   'url': 'https://www.petfinder.com/horse/peter-pony-70172509/ga/cumming/save-the-horses-ga33/?referrer_id=faba0c62-7796-4d66-aba9-6ae4db9b200c&utm_source=api&utm_medium=partnership&utm_content=faba0c62-7796-4d66-aba9-6ae4db9b200c',
   'type': 'Horse',
   'species': 'Pony',
   'breeds': {'primary': 'Pony',
    'secondary': None,
    'mixed': False,
    'unknown': False},
   'colors': {'primary': 'Chestnut / Sorrel',
    'secondary': None,
    'tertiary': None},
   'age': 'Senior',
   'gender': 'Male',
   'size': 'Small',
   'coat': None,
   'attributes': {'spayed_neutered': True,
    'house_trained': False,
    'declawed': None,
    'special_needs': True,
    'shots_current': True},
   'environment': {'children': True, 'dogs': True, 'cats': True},
   'tags': ['Friendly', 'Affectionate', 'Quiet', 'Gentle'],
   'name': 'Peter Pony',
   'description': '24 yo gelding, 14 hands. He lives on 10 acres and is such a good boy. Such a 

In [38]:
# Get initial response
response = requests.get(base_url, headers=headers, params=params)

# Check if the initial response is successful
if response.status_code != 200:
    print(f"Failed: {response.status_code}")
else:
# Get Json and extract pagination info
    res = response.json()
    pagination_info = res.get('pagination', {})
    total_pages = pagination_info.get('total_pages', 0)
    all_pages = []

# Store data from response
    if 'animals' in res:
        all_pages.extend(res['animals'])

# Loop through remaining pages and retrieve data
    for page_num in range(2, total_pages + 1): # From page 2
        params['page'] = page_num
        for attempt in range(11): 
            response = requests.get(base_url, headers=headers, params=params)
            if response.status_code == 200:
                res = response.json()
                if 'animals' in res:
                    all_pages.extend(res['animals'])
                break
            else:
                if attempt == 10:
                    print(f"Page {page_num} failed after retries.")
                break

    print("Successful")
    print(len(all_pages))
    print(f"Total Pages: {total_pages}")

Successful
115
Total Pages: 2


In [39]:
horse2 = json_normalize(all_pages)
print(horse2.shape)
horse2.head()

(115, 49)


id organization_id  \
0  70172509            GA33   
1  70159363           MO209   
2  70158898           MO209   
3  70151832           MO209   
4  70151831           MO209   

                                                 url   type species     age  \
0  https://www.petfinder.com/horse/peter-pony-701...  Horse    Pony  Senior   
1  https://www.petfinder.com/horse/tessa-70159363...  Horse    Pony   Adult   
2  https://www.petfinder.com/horse/rufio-70158898...  Horse   Horse   Adult   
3  https://www.petfinder.com/horse/dandy-70151832...  Horse   Horse   Young   
4  https://www.petfinder.com/horse/malone-7015183...  Horse   Horse   Young   

   gender         size  coat                                     tags  \
0    Male        Small  None  [Friendly, Affectionate, Quiet, Gentle]   
1  Female  Extra Large  None                                       []   
2    Male  Extra Large  None                                       []   
3  Female  Extra Large  None                                       []   
4    Male  Extra Large  None                                       []   

         name                                        description  \
0  Peter Pony  24 yo gelding, 14 hands. He lives on 10 acres ...   
1       TESSA  Little Miss Tessa came to Longmeadow with anot...   
2       RUFIO  Rufio is a handsome 18-year-old Quarter Horse ...   
3       DANDY  Sweet Dandy came to Longmeadow malnourished an...   
4      MALONE  Mr. Malone came to Longmeadow in the early spr...   

  organization_animal_id                                             photos  \
0                   None  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
1                A728698  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
2                A729968  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
3                A727525  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
4                A697582  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   

  videos     status         status_changed_at              published_at  \
0     []  adoptable  2023-12-28T17:07:35+0000  2023-12-28T17:07:34+0000   
1     []  adoptable  2023-12-27T15:58:52+0000  2023-12-27T15:58:50+0000   
2     []  adoptable  2023-12-27T14:59:26+0000  2023-12-27T14:59:24+0000   
3     []  adoptable  2023-12-26T18:58:15+0000  2023-12-26T18:58:13+0000   
4     []  adoptable  2023-12-26T18:58:16+0000  2023-12-26T18:58:13+0000   

   distance breeds.primary breeds.secondary  breeds.mixed  breeds.unknown  \
0  193.9479           Pony             None         False           False   
1  280.6533           Pony             None         False           False   
2  280.6533   Quarterhorse             None         False           False   
3  280.6533          Grade             None         False           False   
4  280.6533     Saddlebred             None         False           False   

      colors.primary colors.secondary colors.tertiary  \
0  Chestnut / Sorrel             None            None   
1               None             None            None   
2               None             None            None   
3               None             None            None   
4               None             None            None   

   attributes.spayed_neutered  attributes.house_trained attributes.declawed  \
0                        True                     False                None   
1                       False                     False                None   
2                        True                     False                None   
3                       False                     False                None   
4                        True                     False                None   

   attributes.special_needs  attributes.shots_current environment.children  \
0                      True                      True                 True   
1                     False                     False                 None   
2                     False                     False     

In [41]:
horse2 = horse2[horse2['contact.address.state']=='TN']
horse2.shape

(2, 49)

In [42]:
# Combine both dataframes
horse = pd.concat([horse, horse2], axis=1)
horse.shape

(16, 99)

In [43]:
# Export to CSV
horse.to_csv('../data/horses.csv', index=False)

## Adopted Barnyard Animals

In [44]:
# Get token
token_url = 'https://api.petfinder.com/v2/oauth2/token'
token_data = {
    'grant_type': 'client_credentials',
    'client_id': key,
    'client_secret': secret
}

# Send post request to get token & extract token
response = requests.post(token_url, data=token_data)
access_token = response.json()['access_token']

# Create base url & headers with token access
base_url = 'https://api.petfinder.com/v2/animals'
headers = {'Authorization': f'Bearer {access_token}'}

# Create parameters
params = {
    'type' : 'barnyard',
    'status': 'adopted', 
    'before': '2023-12-31T23:59:59+00:00',
    'after': '2023-01-01T00:00:00+00:00',
    'location': 'Nashville, TN',
    'distance': 300,
    'limit': 100 
}

response = requests.get(base_url, headers=headers, params=params)
res = response.json()
print(response)
res

<Response [200]>


{'animals': [{'id': 70204542,
   'organization_id': 'TN974',
   'url': 'https://www.petfinder.com/barnyard/destiny-70204542/tn/nashville/fabled-farm-rescue-and-sanctuary-tn974/?referrer_id=faba0c62-7796-4d66-aba9-6ae4db9b200c&utm_source=api&utm_medium=partnership&utm_content=faba0c62-7796-4d66-aba9-6ae4db9b200c',
   'type': 'Barnyard',
   'species': 'Pot Bellied',
   'breeds': {'primary': 'Vietnamese Pot Bellied',
    'secondary': None,
    'mixed': False,
    'unknown': False},
   'colors': {'primary': 'Black', 'secondary': None, 'tertiary': None},
   'age': 'Baby',
   'gender': 'Female',
   'size': 'Small',
   'coat': 'Short',
   'attributes': {'spayed_neutered': True,
    'house_trained': False,
    'declawed': None,
    'special_needs': False,
    'shots_current': True},
   'environment': {'children': True, 'dogs': True, 'cats': True},
   'tags': ['Friendly',
    'Affectionate',
    'Playful',
    'Smart',
    'Curious',
    'Funny'],
   'name': 'Destiny',
   'description': 'It mig

In [45]:
# Get initial response
response = requests.get(base_url, headers=headers, params=params)

# Check if the initial response is successful
if response.status_code != 200:
    print(f"Failed: {response.status_code}")
else:
    res = response.json()
    pagination_info = res.get('pagination', {})
    total_pages = pagination_info.get('total_pages', 0)
    all_pages = []

    if 'animals' in res:
        all_pages.extend(res['animals'])

    for page_num in range(2, total_pages + 1):
        params['page'] = page_num
        for attempt in range(11): 
            response = requests.get(base_url, headers=headers, params=params)
            if response.status_code == 200:
                res = response.json()
                if 'animals' in res:
                    all_pages.extend(res['animals'])
                break
            else:
                if attempt == 10:
                    print(f"Page {page_num} failed after retries.")
                break

    print("Successful")
    print(len(all_pages))
    print(f"Total Pages: {total_pages}")

Successful
65
Total Pages: 1


In [46]:
barnyard = json_normalize(all_pages)
#barnyard.head()

In [47]:
barnyard = barnyard[barnyard['contact.address.state']=='TN']
barnyard.shape

(27, 50)

## Adoptable Barnyard Animals

In [48]:
# Get token
token_url = 'https://api.petfinder.com/v2/oauth2/token'
token_data = {
    'grant_type': 'client_credentials',
    'client_id': key,
    'client_secret': secret
}

# Send post request to get token & extract token
response = requests.post(token_url, data=token_data)
access_token = response.json()['access_token']

# Create base url & headers with token access
base_url = 'https://api.petfinder.com/v2/animals'
headers = {'Authorization': f'Bearer {access_token}'}

# Create parameters
params = {
    'type': 'barnyard',
    'status': 'adoptable', #changed parameter
    'before': '2023-12-31T23:59:59+00:00',
    'after': '2023-01-01T00:00:00+00:00',
    'location': 'Nashville, TN',
    'distance': 300,
    'limit': 100 
}

response = requests.get(base_url, headers=headers, params=params)
res = response.json()
print(response)
res

<Response [200]>


{'animals': [{'id': 69777412,
   'organization_id': 'IN738',
   'url': 'https://www.petfinder.com/barnyard/henry-69777412/in/brownsburg/oinking-acres-farm-rescue-and-sanctuary-inc-in738/?referrer_id=faba0c62-7796-4d66-aba9-6ae4db9b200c&utm_source=api&utm_medium=partnership&utm_content=faba0c62-7796-4d66-aba9-6ae4db9b200c',
   'type': 'Barnyard',
   'species': 'Goat',
   'breeds': {'primary': 'Pygmy',
    'secondary': None,
    'mixed': False,
    'unknown': False},
   'colors': {'primary': None, 'secondary': None, 'tertiary': None},
   'age': 'Young',
   'gender': 'Male',
   'size': 'Medium',
   'coat': None,
   'attributes': {'spayed_neutered': True,
    'house_trained': False,
    'declawed': None,
    'special_needs': False,
    'shots_current': True},
   'environment': {'children': True, 'dogs': None, 'cats': True},
   'tags': [],
   'name': 'Henry ',
   'description': 'Meet Henry! This cutie with the funny looking hair was picked up as a stray by Henry County Animal Control....',


In [49]:
# Get initial response
response = requests.get(base_url, headers=headers, params=params)

# Check if the initial response is successful
if response.status_code != 200:
    print(f"Failed: {response.status_code}")
else:
    res = response.json()
    pagination_info = res.get('pagination', {})
    total_pages = pagination_info.get('total_pages', 0)
    all_pages = []

    if 'animals' in res:
        all_pages.extend(res['animals'])

    for page_num in range(2, total_pages + 1):
        params['page'] = page_num
        for attempt in range(16): 
            response = requests.get(base_url, headers=headers, params=params)
            if response.status_code == 200:
                res = response.json()
                if 'animals' in res:
                    all_pages.extend(res['animals'])
                break
            else:
                if attempt == 15:
                    print(f"Page {page_num} failed after retries.")
                break

    print("Successful")
    print(len(all_pages))
    print(f"Total Pages: {total_pages}")

Successful
38
Total Pages: 1


In [50]:
barnyard2 = json_normalize(all_pages)
print(barnyard2.shape)
barnyard2.head()

(38, 50)


id organization_id  \
0  69777412           IN738   
1  69777321           IN738   
2  69777064           IN738   
3  69776938           IN738   
4  69752339           GA827   

                                                 url      type      species  \
0  https://www.petfinder.com/barnyard/henry-69777...  Barnyard         Goat   
1  https://www.petfinder.com/barnyard/tommy-and-j...  Barnyard         Goat   
2  https://www.petfinder.com/barnyard/darla-and-g...  Barnyard         Goat   
3  https://www.petfinder.com/barnyard/jack-and-ji...  Barnyard         Goat   
4  https://www.petfinder.com/barnyard/pepper-6975...  Barnyard  Pot Bellied   

     age gender    size   coat        tags               name  \
0  Young   Male  Medium   None          []             Henry    
1  Adult   Male   Large   None          []   Tommy and Jimmy    
2  Adult   Male  Medium   None          []  Darla and Gilber    
3  Adult   Male   Small   None          []      Jack and Jim    
4  Young   Male  Medium  Short  [Friendly]             Pepper   

                                         description organization_animal_id  \
0  Meet Henry! This cutie with the funny looking ...                   None   
1  Meet Tommy and his twin brother Jimmy. They ar...                   None   
2  Meet Darla (female grey/white) and Gilber (bla...                   None   
3  Meet Jim and Jack! These boys have been with u...                   None   
4  Meet Mr.Pepper!! \n\nFrom Peppers foster: \n\n...                   None   

                                              photos videos     status  \
0  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adoptable   
1  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adoptable   
2  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adoptable   
3  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adoptable   
4  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adoptable   

          status_changed_at              published_at  distance  \
0  2023-11-22T19:51:33+0000  2023-11-22T19:51:32+0000  254.9598   
1  2023-11-22T19:47:33+0000  2023-11-22T19:47:32+0000  254.9598   
2  2023-11-22T19:43:16+0000  2023-11-22T19:43:15+0000  254.9598   
3  2023-11-22T19:33:08+0000  2023-11-22T19:33:07+0000  254.9598   
4  2023-11-20T22:01:48+0000  2023-11-20T22:01:47+0000  231.7627   

   breeds.primary breeds.secondary  breeds.mixed  breeds.unknown  \
0           Pygmy             None         False           False   
1           Pygmy             None         False           False   
2           Pygmy             None         False           False   
3  Nigerian Dwarf             None         False           False   
4     Pot Bellied             None         False           False   

  colors.primary colors.secondary colors.tertiary  attributes.spayed_neutered  \
0           None             None            None                        True   
1           None             None            None                        True   
2           None             None            None                        True   
3           None             None            None                        True   
4          Black             None            None                        True   

   attributes.house_trained attributes.declawed  attributes.special_needs  \
0                     False                None                     False   
1                     False                None                     False   
2                     False                None                     False   
3                     False                None                     False   
4                     False                None                     False   

   attributes.shots_current environment.children environment.dogs  \
0                      True                 True             None   
1                      True                 True             None   
2                      True                 True             None  

In [51]:
barnyard2 = barnyard2[barnyard2['contact.address.state']=='TN']
barnyard2.shape

(0, 50)

In [52]:
barnyard = pd.concat([barnyard, barnyard2], axis=1)

In [53]:
barnyard.shape

(27, 100)

In [54]:
# Export to CSV
barnyard.to_csv('../data/barnyard.csv', index=False)

## Adopted Rabbits

In [55]:
# Get token
token_url = 'https://api.petfinder.com/v2/oauth2/token'
token_data = {
    'grant_type': 'client_credentials',
    'client_id': key,
    'client_secret': secret
}

# Send post request to get token & extract token
response = requests.post(token_url, data=token_data)
access_token = response.json()['access_token']

# Create base url & headers with token access
base_url = 'https://api.petfinder.com/v2/animals'
headers = {'Authorization': f'Bearer {access_token}'}

# Create parameters
params = {
    'type' : 'rabbit',
    'status': 'adopted', 
    'before': '2023-12-31T23:59:59+00:00',
    'after': '2023-01-01T00:00:00+00:00',
    'location': 'Nashville, TN',
    'distance': 300,
    'limit': 100 
}

response = requests.get(base_url, headers=headers, params=params)
res = response.json()
print(response)
res

<Response [200]>


{'animals': [{'id': 70199176,
   'organization_id': 'KY56',
   'url': 'https://www.petfinder.com/rabbit/clover-70199176/ky/glasgow/barren-river-animal-welfare-association-ky56/?referrer_id=faba0c62-7796-4d66-aba9-6ae4db9b200c&utm_source=api&utm_medium=partnership&utm_content=faba0c62-7796-4d66-aba9-6ae4db9b200c',
   'type': 'Rabbit',
   'species': 'Rabbit',
   'breeds': {'primary': 'Lionhead',
    'secondary': None,
    'mixed': False,
    'unknown': False},
   'colors': {'primary': 'Tan', 'secondary': None, 'tertiary': None},
   'age': 'Adult',
   'gender': 'Male',
   'size': 'Medium',
   'coat': 'Long',
   'attributes': {'spayed_neutered': False,
    'house_trained': False,
    'declawed': None,
    'special_needs': False,
    'shots_current': False},
   'environment': {'children': None, 'dogs': None, 'cats': None},
   'tags': [],
   'name': 'Clover',
   'description': 'Clover came in as a stray through Animal Control on 12/28/2023. His adoption fee is $40.',
   'organization_animal_

In [56]:
# Get initial response
response = requests.get(base_url, headers=headers, params=params)

# Check if the initial response is successful
if response.status_code != 200:
    print(f"Failed: {response.status_code}")
else:
    res = response.json()
    pagination_info = res.get('pagination', {})
    total_pages = pagination_info.get('total_pages', 0)
    all_pages = []

    if 'animals' in res:
        all_pages.extend(res['animals'])

    for page_num in range(2, total_pages + 1):
        params['page'] = page_num
        for attempt in range(11): 
            response = requests.get(base_url, headers=headers, params=params)
            if response.status_code == 200:
                res = response.json()
                if 'animals' in res:
                    all_pages.extend(res['animals'])
                break
            else:
                if attempt == 10:
                    print(f"Page {page_num} failed after retries.")
                break

    print("Successful")
    print(len(all_pages))
    print(f"Total Pages: {total_pages}")

Successful
1020
Total Pages: 11


In [57]:
rabbits = json_normalize(all_pages)
rabbits.head()

id organization_id  \
0  70199176            KY56   
1  70156129           TN801   
2  70071371          TN1000   
3  70132091           TN801   
4  69970401          TN1000   

                                                 url    type species    age  \
0  https://www.petfinder.com/rabbit/clover-701991...  Rabbit  Rabbit  Adult   
1  https://www.petfinder.com/rabbit/rebecca-70156...  Rabbit  Rabbit  Young   
2  https://www.petfinder.com/rabbit/persy-7007137...  Rabbit  Rabbit  Young   
3  https://www.petfinder.com/rabbit/stormy-701320...  Rabbit  Rabbit   Baby   
4  https://www.petfinder.com/rabbit/einstein-6997...  Rabbit  Rabbit  Young   

   gender    size   coat                                               tags  \
0    Male  Medium   Long                                                 []   
1  Female  Medium  Short  [Friendly, Affectionate, Gentle, Playful, Curi...   
2  Female   Large  Short  [Friendly, Smart, Affectionate, Loyal, Gentle,...   
3  Female  Medium  Short  [Friendly, Loyal, Playful, Gentle, Smart, Funn...   
4    Male  Medium   Long  [Friendly, Affectionate, Gentle, Brave, Curiou...   

       name                                        description  \
0    Clover  Clover came in as a stray through Animal Contr...   
1  Rebecca   Hi my name is Rebecca, I am a young American s...   
2     Persy  Persy is a big lady looking for her forever ho...   
3   Stormy   Hi my name is Stormy, I am an American 12 week...   
4  Einstein  Einstein is a special guy looking for a specia...   

  organization_animal_id                                             photos  \
0               54585107  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
1                   None  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
2                   None  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
3                   None  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
4                   None  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   

  videos   status         status_changed_at              published_at  \
0     []  adopted  2024-01-09T18:29:41+0000  2023-12-30T21:04:38+0000   
1     []  adopted  2024-02-04T23:39:41+0000  2023-12-27T01:16:25+0000   
2     []  adopted  2024-01-18T01:43:21+0000  2023-12-26T06:35:40+0000   
3     []  adopted  2024-01-23T16:01:29+0000  2023-12-23T00:05:04+0000   
4     []  adopted  2024-01-07T22:58:46+0000  2023-12-22T21:08:28+0000   

   distance breeds.primary breeds.secondary  breeds.mixed  breeds.unknown  \
0   74.2072       Lionhead             None         False           False   
1  120.4751       American             None         False           False   
2  174.4260    New Zealand    Flemish Giant          True           False   
3  120.4751       American             None         False           False   
4  151.6695       Lionhead             None         False           False   

  colors.primary   colors.secondary colors.tertiary  \
0            Tan               None            None   
1            Tan              White            None   
2    Blue / Gray               None            None   
3          Black  Brown / Chocolate            None   
4          White               None            None   

   attributes.spayed_neutered  attributes.house_trained attributes.declawed  \
0                       False                     False                None   
1                       False                      True                None   
2                        True                     False                None   
3                       False                      True                None   
4                        True                      True                None   

   attributes.special_needs  attributes.shots_current environment.children  \
0                     False                     False                 None   
1                     False                     False                 True   
2                     False                      True     

In [58]:
rabbits.groupby('contact.address.state')['id'].count()

contact.address.state
AL     46
AR      2
GA     36
IL     24
IN     20
KY    758
MO      9
MS      6
NC      9
OH     22
SC      3
TN     85
Name: id, dtype: int64

In [59]:
rabbits = rabbits[rabbits['contact.address.state']=='TN']
rabbits.shape

(85, 50)

## Adoptable Rabbits

In [60]:
# Get token
token_url = 'https://api.petfinder.com/v2/oauth2/token'
token_data = {
    'grant_type': 'client_credentials',
    'client_id': key,
    'client_secret': secret
}

# Send post request to get token & extract token
response = requests.post(token_url, data=token_data)
access_token = response.json()['access_token']

# Create base url & headers with token access
base_url = 'https://api.petfinder.com/v2/animals'
headers = {'Authorization': f'Bearer {access_token}'}

# Create parameters
params = {
    'type': 'rabbit',
    'status': 'adoptable', #changed parameter
    'before': '2023-12-31T23:59:59+00:00',
    'after': '2023-01-01T00:00:00+00:00',
    'location': 'Nashville, TN',
    'distance': 300,
    'limit': 100 
}

response = requests.get(base_url, headers=headers, params=params)
res = response.json()
print(response)
res

<Response [200]>


{'animals': [{'id': 70192849,
   'organization_id': 'KY61',
   'url': 'https://www.petfinder.com/rabbit/britches-70192849/ky/lexington/lexington-humane-society-ky61/?referrer_id=faba0c62-7796-4d66-aba9-6ae4db9b200c&utm_source=api&utm_medium=partnership&utm_content=faba0c62-7796-4d66-aba9-6ae4db9b200c',
   'type': 'Rabbit',
   'species': 'Rabbit',
   'breeds': {'primary': 'Dutch',
    'secondary': None,
    'mixed': True,
    'unknown': False},
   'colors': {'primary': None, 'secondary': None, 'tertiary': None},
   'age': 'Baby',
   'gender': 'Male',
   'size': 'Medium',
   'coat': None,
   'attributes': {'spayed_neutered': True,
    'house_trained': False,
    'declawed': None,
    'special_needs': False,
    'shots_current': True},
   'environment': {'children': None, 'dogs': None, 'cats': None},
   'tags': [],
   'name': 'Britches',
   'description': 'Primary Color: Black Secondary Color: White Age: 0yrs 5mths 1wks Animal has been Neutered',
   'organization_animal_id': '262081',
   

In [61]:
# Get initial response
response = requests.get(base_url, headers=headers, params=params)

# Check if the initial response is successful
if response.status_code != 200:
    print(f"Failed: {response.status_code}")
else:
    res = response.json()
    pagination_info = res.get('pagination', {})
    total_pages = pagination_info.get('total_pages', 0)
    all_pages = []

    if 'animals' in res:
        all_pages.extend(res['animals'])

    for page_num in range(2, total_pages + 1):
        params['page'] = page_num
        for attempt in range(16): 
            response = requests.get(base_url, headers=headers, params=params)
            if response.status_code == 200:
                res = response.json()
                if 'animals' in res:
                    all_pages.extend(res['animals'])
                break
            else:
                if attempt == 15:
                    print(f"Page {page_num} failed after retries.")
                break

    print("Successful")
    print(len(all_pages))
    print(f"Total Pages: {total_pages}")

Successful
238
Total Pages: 3


In [62]:
rabbits2 = json_normalize(all_pages)
print(rabbits2.shape)
rabbits2.head()

(238, 49)


id organization_id  \
0  70192849            KY61   
1  70169322            IN57   
2  70167513           WV249   
3  70166959           IN440   
4  70091102          TN1000   

                                                 url    type species     age  \
0  https://www.petfinder.com/rabbit/britches-7019...  Rabbit  Rabbit    Baby   
1  https://www.petfinder.com/rabbit/florence-7016...  Rabbit  Rabbit   Adult   
2  https://www.petfinder.com/rabbit/kanin-7016751...  Rabbit  Rabbit  Senior   
3  https://www.petfinder.com/rabbit/winter-701669...  Rabbit  Rabbit   Young   
4  https://www.petfinder.com/rabbit/angela-martin...  Rabbit  Rabbit   Young   

   gender    size   coat                                               tags  \
0    Male  Medium   None                                                 []   
1  Female   Large   None                                                 []   
2    Male  Medium   Long            [Friendly, Playful, Smart, Independent]   
3  Female  Medium  Short               [Friendly, Gentle, Playful, Curious]   
4  Female   Large  Short  [Friendly, Affectionate, Playful, Curious, Dig...   

            name                                        description  \
0       Britches  Primary Color: Black Secondary Color: White Ag...   
1       Florence  To find out more about Florence , visit http:/...   
2          Kanin  Kanin is a 5-year-old lionhead rabbit. He has ...   
3         Winter  Meet Winter! Winter was found as a stray by a ...   
4  Angela Martin  Angela Martin is looking for her forever home!...   

  organization_animal_id                                             photos  \
0                 262081  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
1                   4757  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
2              BBRA-A-14  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
3                   None  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
4                   None  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   

  videos     status         status_changed_at              published_at  \
0     []  adoptable  2023-12-30T02:32:11+0000  2023-12-30T02:32:03+0000   
1     []  adoptable  2023-12-28T06:00:36+0000  2023-12-28T06:00:33+0000   
2     []  adoptable  2023-12-28T01:21:42+0000  2023-12-28T01:21:41+0000   
3     []  adoptable  2023-12-28T00:33:11+0000  2023-12-28T00:33:08+0000   
4     []  adoptable  2023-12-26T21:41:11+0000  2023-12-26T21:41:10+0000   

   distance breeds.primary breeds.secondary  breeds.mixed  breeds.unknown  \
0  180.0951          Dutch             None          True           False   
1  247.9073    Californian             None         False           False   
2  285.3111       Lionhead             None         False           False   
3  243.7247      Harlequin             None         False           False   
4  174.4260    New Zealand    Flemish Giant          True           False   

  colors.primary   colors.secondary colors.tertiary  \
0           None               None            None   
1           None               None            None   
2          Black               None            None   
3           None               None            None   
4         Agouti  Brown / Chocolate            None   

   attributes.spayed_neutered  attributes.house_trained attributes.declawed  \
0                        True                     False                None   
1                        True                      True                None   
2                        True                     False                None   
3                        True                      True                None   
4                        True                      True                None   

   attributes.special_needs  attributes.shots_current environment.children  \
0                     False                      True                 None   
1                     False                      True                 None   
2         

In [63]:
rabbits2 = rabbits2[rabbits2['contact.address.state']=='TN']
rabbits2.shape

(23, 49)

In [64]:
rabbits = pd.concat([rabbits, rabbits2], axis=1)
rabbits.shape

(105, 99)

In [65]:
# Export to CSV
rabbits.to_csv('../data/rabbits.csv', index=False)

## Adopted Scales, Fins, & Others

In [66]:
# Get token
token_url = 'https://api.petfinder.com/v2/oauth2/token'
token_data = {
    'grant_type': 'client_credentials',
    'client_id': key,
    'client_secret': secret
}

# Send post request to get token & extract token
response = requests.post(token_url, data=token_data)
access_token = response.json()['access_token']

# Create base url & headers with token access
base_url = 'https://api.petfinder.com/v2/animals'
headers = {'Authorization': f'Bearer {access_token}'}

# Create parameters
params = {
    'type' : 'scales, fins & other',
    'status': 'adopted', 
    'before': '2023-12-31T23:59:59+00:00',
    'after': '2023-01-01T00:00:00+00:00',
    'location': 'Nashville, TN',
    'distance': 300,
    'limit': 100 
}

response = requests.get(base_url, headers=headers, params=params)
res = response.json()
print(response)
res

<Response [200]>


{'animals': [{'id': 69783002,
   'organization_id': 'OH1174',
   'url': 'https://www.petfinder.com/scales-fins-others/courtesy-post-george-69783002/oh/cincinnati/the-ohio-pet-sanctuary-oh1174/?referrer_id=faba0c62-7796-4d66-aba9-6ae4db9b200c&utm_source=api&utm_medium=partnership&utm_content=faba0c62-7796-4d66-aba9-6ae4db9b200c',
   'type': 'Scales, Fins & Other',
   'species': 'Reptile',
   'breeds': {'primary': 'Lizard',
    'secondary': None,
    'mixed': False,
    'unknown': False},
   'colors': {'primary': None, 'secondary': None, 'tertiary': None},
   'age': 'Adult',
   'gender': 'Unknown',
   'size': 'Small',
   'coat': None,
   'attributes': {'spayed_neutered': False,
    'house_trained': False,
    'declawed': None,
    'special_needs': False,
    'shots_current': False},
   'environment': {'children': None, 'dogs': None, 'cats': None},
   'tags': [],
   'name': 'Courtesy Post: George',
   'description': 'George is a peachy color, and is around 1 year old. He is about 6 inches

In [67]:
# Get initial response
response = requests.get(base_url, headers=headers, params=params)

# Check if the initial response is successful
if response.status_code != 200:
    print(f"Failed: {response.status_code}")
else:
    res = response.json()
    pagination_info = res.get('pagination', {})
    total_pages = pagination_info.get('total_pages', 0)
    all_pages = []

    if 'animals' in res:
        all_pages.extend(res['animals'])

    for page_num in range(2, total_pages + 1):
        params['page'] = page_num
        for attempt in range(11): 
            response = requests.get(base_url, headers=headers, params=params)
            if response.status_code == 200:
                res = response.json()
                if 'animals' in res:
                    all_pages.extend(res['animals'])
                break
            else:
                if attempt == 10:
                    print(f"Page {page_num} failed after retries.")
                break

    print("Successful")
    print(len(all_pages))
    print(f"Total Pages: {total_pages}")

Successful
15
Total Pages: 1


In [68]:
scales = json_normalize(all_pages)
print(scales.shape)
scales.head()

(15, 49)


id organization_id  \
0  69783002          OH1174   
1  69782994          OH1174   
2  69770119           MO764   
3  66656405            MS51   
4  65276631           MO764   

                                                 url                  type  \
0  https://www.petfinder.com/scales-fins-others/c...  Scales, Fins & Other   
1  https://www.petfinder.com/scales-fins-others/c...  Scales, Fins & Other   
2  https://www.petfinder.com/scales-fins-others/s...  Scales, Fins & Other   
3  https://www.petfinder.com/scales-fins-others/m...  Scales, Fins & Other   
4  https://www.petfinder.com/scales-fins-others/s...  Scales, Fins & Other   

        species    age   gender    size  coat  \
0       Reptile  Adult  Unknown   Small  None   
1       Reptile  Adult  Unknown   Small  None   
2       Reptile   Baby  Unknown  Medium  None   
3  Other Animal  Young     Male   Small  None   
4      Tortoise  Adult  Unknown  Medium  None   

                                        tags                   name  \
0                                         []  Courtesy Post: George   
1                                         []    Courtesy Post: Nemo   
2  [Friendly, Affectionate, Gentle, Curious]                Stewpot   
3                                         []             Mad Hatter   
4       [Friendly, Gentle, Quiet, Dignified]            Stroganoff    

                                         description organization_animal_id  \
0  George is a peachy color, and is around 1 year...                   None   
1  Nemo is the one with yellow with brown stripes...                   None   
2  Little Stewpot is looking for a home of his ow...                   None   
3  Mad Hatter is the only Guinea Pig left. He is ...                   None   
4  Stroganoff is a Russian Tortoise that is looki...                   None   

                                              photos videos   status  \
0  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
1  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
2  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
3  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
4  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   

          status_changed_at              published_at  distance  \
0  2023-11-23T20:13:18+0000  2023-11-23T02:09:35+0000  241.5267   
1  2023-11-23T20:13:18+0000  2023-11-23T02:08:28+0000  241.5267   
2  2023-12-01T23:29:10+0000  2023-11-22T03:38:15+0000  180.2650   
3  2023-08-29T13:23:24+0000  2023-08-28T15:33:51+0000  201.3685   
4  2024-01-20T04:34:30+0000  2023-07-03T01:13:04+0000  180.2650   

   breeds.primary breeds.secondary  breeds.mixed  breeds.unknown  \
0          Lizard             None         False           False   
1          Lizard             None         False           False   
2  Bearded Dragon             None         False           False   
3           Other             None         False           False   
4         Russian             None         False           False   

  colors.primary colors.secondary colors.tertiary  attributes.spayed_neutered  \
0           None             None            None                       False   
1           None             None            None                       False   
2          Brown             None            None                       False   
3          Brown            White            None                       False   
4          Brown              Tan            None                       False   

   attributes.house_trained attributes.declawed  attributes.special_needs  \
0                     False                None                     False   
1                     False                None                     False   
2                     False                None                     False   
3                     False                None                     False   
4                     False            

In [69]:
scales = scales[scales['contact.address.state']=='TN']
scales.shape

(0, 49)

## Adoptable Scales, Fins, & Others

In [70]:
# Get token
token_url = 'https://api.petfinder.com/v2/oauth2/token'
token_data = {
    'grant_type': 'client_credentials',
    'client_id': key,
    'client_secret': secret
}

# Send post request to get token & extract token
response = requests.post(token_url, data=token_data)
access_token = response.json()['access_token']

# Create base url & headers with token access
base_url = 'https://api.petfinder.com/v2/animals'
headers = {'Authorization': f'Bearer {access_token}'}

# Create parameters
params = {
    'type': 'scales, fins & other',
    'status': 'adoptable', #changed parameter
    'before': '2023-12-31T23:59:59+00:00',
    'after': '2023-01-01T00:00:00+00:00',
    'location': 'Nashville, TN',
    'distance': 300,
    'limit': 100 
}

response = requests.get(base_url, headers=headers, params=params)
res = response.json()
print(response)
res

<Response [200]>


{'animals': [{'id': 70141686,
   'organization_id': 'OH1174',
   'url': 'https://www.petfinder.com/scales-fins-others/ivan-70141686/oh/cincinnati/the-ohio-pet-sanctuary-oh1174/?referrer_id=faba0c62-7796-4d66-aba9-6ae4db9b200c&utm_source=api&utm_medium=partnership&utm_content=faba0c62-7796-4d66-aba9-6ae4db9b200c',
   'type': 'Scales, Fins & Other',
   'species': 'Reptile',
   'breeds': {'primary': 'Gecko',
    'secondary': None,
    'mixed': False,
    'unknown': False},
   'colors': {'primary': None, 'secondary': None, 'tertiary': None},
   'age': 'Adult',
   'gender': 'Male',
   'size': 'Small',
   'coat': None,
   'attributes': {'spayed_neutered': False,
    'house_trained': False,
    'declawed': None,
    'special_needs': False,
    'shots_current': False},
   'environment': {'children': None, 'dogs': None, 'cats': None},
   'tags': [],
   'name': 'Ivan',
   'description': 'Ivan came to us because of life changes for the owner. At 2 years old this Leopard Gecko has a...',
   'organ

In [71]:
# Get initial response
response = requests.get(base_url, headers=headers, params=params)

# Check if the initial response is successful
if response.status_code != 200:
    print(f"Failed: {response.status_code}")
else:
    res = response.json()
    pagination_info = res.get('pagination', {})
    total_pages = pagination_info.get('total_pages', 0)
    all_pages = []

    if 'animals' in res:
        all_pages.extend(res['animals'])

    for page_num in range(2, total_pages + 1):
        params['page'] = page_num
        for attempt in range(16): 
            response = requests.get(base_url, headers=headers, params=params)
            if response.status_code == 200:
                res = response.json()
                if 'animals' in res:
                    all_pages.extend(res['animals'])
                break
            else:
                if attempt == 15:
                    print(f"Page {page_num} failed after retries.")
                break

    print("Successful")
    print(len(all_pages))
    print(f"Total Pages: {total_pages}")

Successful
31
Total Pages: 1


In [72]:
scales2 = json_normalize(all_pages)
print(scales2.shape)
scales2.head()

(31, 50)


id organization_id  \
0  70141686          OH1174   
1  70057771            OH26   
2  70003460            OH26   
3  70003462            OH26   
4  70003466            OH26   

                                                 url                  type  \
0  https://www.petfinder.com/scales-fins-others/i...  Scales, Fins & Other   
1  https://www.petfinder.com/scales-fins-others/v...  Scales, Fins & Other   
2  https://www.petfinder.com/scales-fins-others/c...  Scales, Fins & Other   
3  https://www.petfinder.com/scales-fins-others/r...  Scales, Fins & Other   
4  https://www.petfinder.com/scales-fins-others/s...  Scales, Fins & Other   

   species    age  gender    size  coat tags    name  \
0  Reptile  Adult    Male   Small  None   []    Ivan   
1  Reptile  Adult    Male  Medium  None   []   Venus   
2   Turtle  Adult  Female  Medium  None   []   Chuck   
3  Reptile  Adult    Male  Medium  None   []  Randal   
4  Reptile  Adult  Female  Medium  None   []    Sven   

                                         description organization_animal_id  \
0  Ivan came to us because of life changes for th...                   O237   
1  Hello! I&amp;#39;m looking for a good home. I&...             C230723106   
2  Roughly 5&amp;#34; carapaceAvailable for adopt...             C231210161   
3  I don&amp;#39;t handle the best, but I&amp;#39...             C231210163   
4  I would prefer to be a display animal as I&amp...             C231210162   

                                              photos videos     status  \
0  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adoptable   
1  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adoptable   
2  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adoptable   
3  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adoptable   
4  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adoptable   

          status_changed_at              published_at  distance  \
0  2023-12-24T10:02:49+0000  2023-12-24T10:02:46+0000  241.5267   
1  2023-12-16T10:01:47+0000  2023-12-16T10:01:45+0000  244.7654   
2  2023-12-12T10:26:27+0000  2023-12-12T10:26:24+0000  244.7654   
3  2023-12-12T10:26:27+0000  2023-12-12T10:26:24+0000  244.7654   
4  2023-12-12T10:26:27+0000  2023-12-12T10:26:24+0000  244.7654   

  breeds.primary breeds.secondary  breeds.mixed  breeds.unknown  \
0          Gecko             None         False           False   
1         Lizard             None         False           False   
2         Turtle             None         False           False   
3          Gecko             None         False           False   
4          Gecko             None         False           False   

  colors.primary colors.secondary colors.tertiary  attributes.spayed_neutered  \
0           None             None            None                       False   
1           None             None            None                       False   
2           None             None            None                       False   
3           None             None            None                       False   
4           None             None            None                       False   

   attributes.house_trained attributes.declawed  attributes.special_needs  \
0                     False                None                     False   
1                     False                None                     False   
2                     False                None                     False   
3                     False                None                     False   
4                     False                None                     False   

   attributes.shots_current environment.children environment.dogs  \
0                     False                 None             None   
1                     False                 None             None   
2                     False                 None             None   
3                     False                 None             Non

In [73]:
scales2 = scales2[scales2['contact.address.state']=='TN']
scales2.shape

(2, 50)

In [74]:
scales = pd.concat([scales, scales2], axis=1)

In [75]:
scales.shape

(2, 99)

In [76]:
# Export to CSV
scales.to_csv('../data/scales.csv', index=False)

## Adopted Small & Furry Animals

In [77]:
# Get token
token_url = 'https://api.petfinder.com/v2/oauth2/token'
token_data = {
    'grant_type': 'client_credentials',
    'client_id': key,
    'client_secret': secret
}

# Send post request to get token & extract token
response = requests.post(token_url, data=token_data)
access_token = response.json()['access_token']

# Create base url & headers with token access
base_url = 'https://api.petfinder.com/v2/animals'
headers = {'Authorization': f'Bearer {access_token}'}

# Create parameters
params = {
    'type' : 'small & furry',
    'status': 'adopted', 
    'before': '2023-12-31T23:59:59+00:00',
    'after': '2023-01-01T00:00:00+00:00',
    'location': 'Nashville, TN',
    'distance': 300,
    'limit': 100 
}

response = requests.get(base_url, headers=headers, params=params)
res = response.json()
print(response)
res

<Response [200]>


{'animals': [{'id': 70115100,
   'organization_id': 'OH1174',
   'url': 'https://www.petfinder.com/small-furry/courtesy-post-rats-oddie-felix-and-ramsey-70115100/oh/cincinnati/the-ohio-pet-sanctuary-oh1174/?referrer_id=faba0c62-7796-4d66-aba9-6ae4db9b200c&utm_source=api&utm_medium=partnership&utm_content=faba0c62-7796-4d66-aba9-6ae4db9b200c',
   'type': 'Small & Furry',
   'species': 'Rat',
   'breeds': {'primary': 'Rat',
    'secondary': None,
    'mixed': False,
    'unknown': False},
   'colors': {'primary': None, 'secondary': None, 'tertiary': None},
   'age': 'Senior',
   'gender': 'Male',
   'size': 'Small',
   'coat': None,
   'attributes': {'spayed_neutered': False,
    'house_trained': False,
    'declawed': None,
    'special_needs': False,
    'shots_current': False},
   'environment': {'children': None, 'dogs': None, 'cats': None},
   'tags': [],
   'name': 'Courtesy Post: Rats Oddie, Felix and Ramsey',
   'description': 'Owner name: Jasmine Kongmanychanh\nPhone: 615-713-75

In [78]:
# Get initial response
response = requests.get(base_url, headers=headers, params=params)

# Check if the initial response is successful
if response.status_code != 200:
    print(f"Failed: {response.status_code}")
else:
    res = response.json()
    pagination_info = res.get('pagination', {})
    total_pages = pagination_info.get('total_pages', 0)
    all_pages = []

    if 'animals' in res:
        all_pages.extend(res['animals'])

    for page_num in range(2, total_pages + 1):
        params['page'] = page_num
        for attempt in range(11): 
            response = requests.get(base_url, headers=headers, params=params)
            if response.status_code == 200:
                res = response.json()
                if 'animals' in res:
                    all_pages.extend(res['animals'])
                break
            else:
                if attempt == 10:
                    print(f"Page {page_num} failed after retries.")
                break

    print("Successful")
    print(len(all_pages))
    print(f"Total Pages: {total_pages}")

Successful
509
Total Pages: 6


In [79]:
smallandfurry = json_normalize(all_pages)
smallandfurry.head()

id organization_id  \
0  70115100          OH1174   
1  70085274          OH1167   
2  70067653            TN82   
3  70042767          OH1174   
4  69980426           IN386   

                                                 url           type  \
0  https://www.petfinder.com/small-furry/courtesy...  Small & Furry   
1  https://www.petfinder.com/small-furry/rosa-and...  Small & Furry   
2  https://www.petfinder.com/small-furry/newton-a...  Small & Furry   
3  https://www.petfinder.com/small-furry/courtesy...  Small & Furry   
4  https://www.petfinder.com/small-furry/troy-699...  Small & Furry   

      species     age  gender    size   coat  \
0         Rat  Senior    Male   Small   None   
1  Guinea Pig   Young  Female   Small  Short   
2  Guinea Pig   Adult    Male  Medium  Short   
3  Guinea Pig   Adult  Female   Small  Short   
4  Guinea Pig    Baby    Male  Medium   None   

                                  tags  \
0                                   []   
1  [Sociable, Spunky, Outgoing, Funny]   
2              [Couch potato, Playful]   
3                                   []   
4                                   []   

                                          name  \
0  Courtesy Post: Rats Oddie, Felix and Ramsey   
1                              Rosa and Peanut   
2                            Newton and Butter   
3                 Courtesy Post: Lily and Rose   
4                                         Troy   

                                         description organization_animal_id  \
0  Owner name: Jasmine Kongmanychanh\nPhone: 615-...                   None   
1  Rosa and Peanut are 1 year old females. They a...                   None   
2  Are you looking to add a sweet treat to your h...                   None   
3  Lily and Rose female both have been raised tog...                   None   
4  This little cutie is about 3 weeks old.  He lo...                   None   

                                              photos videos   status  \
0  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
1  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
2  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
3  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   
4  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...     []  adopted   

          status_changed_at              published_at  distance  \
0  2023-12-27T22:07:59+0000  2023-12-21T17:10:38+0000  241.5267   
1  2024-01-02T22:02:00+0000  2023-12-19T02:22:54+0000  258.7470   
2  2024-02-08T15:37:26+0000  2023-12-17T12:55:59+0000  151.6695   
3  2023-12-31T16:11:07+0000  2023-12-15T02:58:41+0000  241.5267   
4  2023-12-28T01:28:13+0000  2023-12-10T04:02:39+0000  164.2851   

  breeds.primary breeds.secondary  breeds.mixed  breeds.unknown  \
0            Rat             None         False           False   
1     Guinea Pig             None         False           False   
2     Guinea Pig             None         False           False   
3   Short-Haired             None         False           False   
4   Short-Haired             None          True           False   

      colors.primary colors.secondary colors.tertiary  \
0               None             None            None   
1  Brown / Chocolate              Tan           White   
2              Black           Calico            None   
3               None             None            None   
4               None             None            None   

   attributes.spayed_neutered  attributes.house_trained attributes.declawed  \
0                       False                     False                None   
1                       False                     False                None   
2                       False                     False                None   
3                       False                     False                None   
4                       False                     False                None   

   attributes.specia

In [80]:
smallandfurry = smallandfurry[smallandfurry['contact.address.state']=='TN']
smallandfurry.shape

(58, 50)

## Adoptable Small & Furry Animals

In [4]:
# Get token
token_url = 'https://api.petfinder.com/v2/oauth2/token'
token_data = {
    'grant_type': 'client_credentials',
    'client_id': key,
    'client_secret': secret
}

# Send post request to get token & extract token
response = requests.post(token_url, data=token_data)
access_token = response.json()['access_token']

# Create base url & headers with token access
base_url = 'https://api.petfinder.com/v2/animals'
headers = {'Authorization': f'Bearer {access_token}'}

# Create parameters
params = {
    'type': 'small & furry',
    'status': 'adoptable', #changed parameter
    'before': '2023-12-31T23:59:59+00:00',
    'after': '2023-01-01T00:00:00+00:00',
    'location': 'Nashville, TN',
    'distance': 300,
    'limit': 100 
}

response = requests.get(base_url, headers=headers, params=params)
res = response.json()
print(response)
res

<Response [200]>


{'animals': [{'id': 70191691,
   'organization_id': 'IN190',
   'url': 'https://www.petfinder.com/small-furry/windsor-70191691/in/evansville/vanderburgh-humane-society-in190/?referrer_id=faba0c62-7796-4d66-aba9-6ae4db9b200c&utm_source=api&utm_medium=partnership&utm_content=faba0c62-7796-4d66-aba9-6ae4db9b200c',
   'type': 'Small & Furry',
   'species': 'Guinea Pig',
   'breeds': {'primary': 'Guinea Pig',
    'secondary': None,
    'mixed': False,
    'unknown': False},
   'colors': {'primary': None, 'secondary': None, 'tertiary': None},
   'age': 'Young',
   'gender': 'Male',
   'size': 'Medium',
   'coat': None,
   'attributes': {'spayed_neutered': False,
    'house_trained': False,
    'declawed': None,
    'special_needs': False,
    'shots_current': True},
   'environment': {'children': None, 'dogs': None, 'cats': None},
   'tags': [],
   'name': 'Windsor',
   'description': None,
   'organization_animal_id': 'VAN-A-45538',
   'photos': [{'small': 'https://dl5zpyw5k3jeb.cloudfront.

In [5]:
# Get initial response
response = requests.get(base_url, headers=headers, params=params)

# Check if the initial response is successful
if response.status_code != 200:
    print(f"Failed: {response.status_code}")
else:
    res = response.json()
    pagination_info = res.get('pagination', {})
    total_pages = pagination_info.get('total_pages', 0)
    all_pages = []

    if 'animals' in res:
        all_pages.extend(res['animals'])

    for page_num in range(2, total_pages + 1):
        params['page'] = page_num
        for attempt in range(16): 
            response = requests.get(base_url, headers=headers, params=params)
            if response.status_code == 200:
                res = response.json()
                if 'animals' in res:
                    all_pages.extend(res['animals'])
                break
            else:
                if attempt == 15:
                    print(f"Page {page_num} failed after retries.")
                break

    print("Successful")
    print(len(all_pages))
    print(f"Total Pages: {total_pages}")

Successful
76
Total Pages: 1


In [83]:
smallandfurry2 = json_normalize(all_pages)
print(smallandfurry2.shape)
smallandfurry2.head()

(80, 50)


id organization_id  \
0  70191691           IN190   
1  70188679           IN190   
2  70188678           IN190   
3  70188676           IN190   
4  70188675           IN190   

                                                 url           type  \
0  https://www.petfinder.com/small-furry/windsor-...  Small & Furry   
1  https://www.petfinder.com/small-furry/grantham...  Small & Furry   
2  https://www.petfinder.com/small-furry/liverpoo...  Small & Furry   
3  https://www.petfinder.com/small-furry/manchest...  Small & Furry   
4  https://www.petfinder.com/small-furry/bristol-...  Small & Furry   

      species    age gender    size  coat tags        name description  \
0  Guinea Pig  Young   Male  Medium  None   []     Windsor        None   
1  Guinea Pig  Young   Male  Medium  None   []    Grantham        None   
2  Guinea Pig  Young   Male  Medium  None   []   Liverpool        None   
3  Guinea Pig  Young   Male  Medium  None   []  Manchester        None   
4  Guinea Pig  Young   Male  Medium  None   []     Bristol        None   

  organization_animal_id                                             photos  \
0            VAN-A-45538  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
1            VAN-A-45537  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
2            VAN-A-45539  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
3            VAN-A-45541  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   
4            VAN-A-45540  [{'small': 'https://dl5zpyw5k3jeb.cloudfront.n...   

  videos     status         status_changed_at              published_at  \
0     []  adoptable  2023-12-30T00:45:51+0000  2023-12-30T00:45:49+0000   
1     []  adoptable  2023-12-29T20:45:54+0000  2023-12-29T20:45:52+0000   
2     []  adoptable  2023-12-29T20:45:54+0000  2023-12-29T20:45:52+0000   
3     []  adoptable  2023-12-29T20:45:54+0000  2023-12-29T20:45:52+0000   
4     []  adoptable  2023-12-29T20:45:54+0000  2023-12-29T20:45:52+0000   

   distance breeds.primary breeds.secondary  breeds.mixed  breeds.unknown  \
0  133.4343     Guinea Pig             None         False           False   
1  133.4343     Guinea Pig             None         False           False   
2  133.4343     Guinea Pig             None         False           False   
3  133.4343     Guinea Pig             None         False           False   
4  133.4343     Guinea Pig             None         False           False   

  colors.primary colors.secondary colors.tertiary  attributes.spayed_neutered  \
0           None             None            None                       False   
1           None             None            None                       False   
2           None             None            None                       False   
3           None             None            None                       False   
4           None             None            None                       False   

   attributes.house_trained attributes.declawed  attributes.special_needs  \
0                     False                None                     False   
1                     False                None                     False   
2                     False                None                     False   
3                     False                None                     False   
4                     False                None                     False   

   attributes.shots_current environment.children environment.dogs  \
0                      True                 None             None   
1                      True                 None             None   
2                      True                 None             None   
3                      True                 None             None   
4                      True                 None             None   

  environment.cats                        primary_photo_cropped.small  \
0             None  https://dl5zpyw5k3jeb.cloudfront.net/photos/pe...   
1             None  https://dl5zpyw5k3jeb.cloudfro

In [84]:
smallandfurry2 = smallandfurry2[smallandfurry2['contact.address.state']=='TN']
smallandfurry2.shape

(5, 50)

In [85]:
smallandfurry = pd.concat([smallandfurry, smallandfurry2], axis=1)
smallandfurry.shape

(63, 100)

In [86]:
# Export to CSV
smallandfurry.to_csv('../data/smallandfurry.csv', index=False)